In [ ]:
%matplotlib qt
import numpy as np
import matplotlib.pyplot as plt
from pynverse import inversefunc
import random
import scipy.misc
from scipy import ndimage

In [ ]:
def V(newLong, newLat, currLong, currLat, scale2):
    scale = 1.2
    deltaLong = curveDistLong(currLong, newLat, scale2)
    deltaLat = curveDistLat(newLong, currLat, scale2)
    v1 = (np.abs(deltaLong) / scale2)**2
    v2 = (np.abs(deltaLat) / scale2)**2
    return v1 + v2

In [ ]:
def P(newLong, newLat, currLong, currLat, scale):
    p = np.exp(-V(newLong, newLat, currLong, currLat, scale))
    return p

In [ ]:
def curveDistLat(long, lat, scale2):
    curveLat = pointDistLat(long, scale2)
    point1 = np.array([long, lat])
    point2 = np.array([long, curveLat])
    dist = np.linalg.norm(point1-point2)
    return dist

In [ ]:
def curveDistLong(long, lat, scale2):
    curveLong = pointDistLong(lat, scale2)
    point1 = np.array([long, lat])
    point2 = np.array([curveLong, lat])
    dist = np.linalg.norm(point1-point2)
    return dist

In [ ]:
def pointDistLat(x, scale2):
    y = (-1363*x**3)/(333011250) + (63913*x**2)/(7400250) - (14560*x)/(2277) + (6254130/3289)
    return int(np.round(y))

In [ ]:
def pointDistLong(x, scale2):
    funcLong = (lambda x: (-1363*x**3)/(333011250) + (63913*x**2)/(7400250) - (14560*x)/(2277) + (6254130/3289))
    invY = inversefunc(funcLong)
    y = invY(x)
    return int(np.round(y))

In [ ]:
N = 800
H = np.zeros((N, N))

from matplotlib.animation import FFMpegWriter
metadata = dict(title='Hurricane Sim', artist='Aron Delevic',comment='Hurricane')
writer = FFMpegWriter(fps=15, metadata=metadata)
fig = plt.figure()
img = plt.imread('map.png')
icon = plt.imread('icon.png')

with writer.saving(fig, "hurricanes.mp4", dpi=200):
    for iter in range(5): #Controls number of storm paths simulated, takes very long to produce animation
        movesX = []
        movesY = []
        currLong = 795 #Initial positions
        currLat = 220
        prevLong = currLong
        prevLat = currLat
        #Random color for storm visual
        rval = np.random.random()
        bval = np.random.random()
        gval = np.random.random()
        grad = (rval, bval, gval)
        count = 0
        countSize = 0
        #Randomness to account for environmental and climate variables
        scale = 1 + random.randint(0,4)
        warmWater = random.randint(0,4)

        #Randomness added because storms might fizzle out
        for numMoves in range((8 + random.randint(0, 4))*N): #Number of proposed moves per simulation of storm
            #Random move proposition creator
            propLong = currLong
            propLat = currLat

            stepSize = 6
            rLong = np.random.random()
            rLat = np.random.random()
            eachStepLong = stepSize * (rLong - 0.5)
            eachStepLat = stepSize * (rLat - 0.5)
            propLong -= int(round(eachStepLong))
            propLat += int(round(eachStepLat))

            #Randomness to account for environmental and climate variables
            propLong -= int(round(3.5*np.random.random()))
            propLat += int(round(3.5*np.random.random()))

            pNew = P(propLong, propLat, currLong, currLat, scale)
            pOld = P(currLong, currLat, prevLong, prevLat, scale)
            pAccept = pNew / pOld

            #Acceptance case
            r = np.random.random()
            if r < pAccept:
                prevLong = currLong
                prevLat = currLat
                currLong = propLong
                currLat = propLat
                count += 1
                #Out of bounds loop break
                if prevLat >= 800:
                    break
            
            #Only plot every 40th
            if count % 40 == 0:
                countSize += 2
                movesX.append(currLong)
                movesY.append(currLat)
            
                #Hurricane icon rotation, size increase and plotting, animation writing done here
                rotIcon = ndimage.rotate(icon, 30*random.randint(1,5))
                implot = plt.imshow(img, extent=[0,800,0,800])
                implot2 = plt.imshow(rotIcon, extent=[currLong-30-countSize,currLong+30+countSize,currLat-30-countSize,currLat+30+countSize])
                plt.xlabel('Longitude')
                plt.ylabel('Latitude')
                plt.title('Hurricane Alley Monte-Carlo Trajectory Simulations')
                plt.xlim([0,800])
                plt.ylim([0,800])
                plt.plot(movesX, movesY, color=grad)
                plt.show()
                plt.draw()
                plt.pause(0.01)
                writer.grab_frame()
    #plt.clf()
